In [30]:
import pandas as pd
import psycopg2
import sqlalchemy
import matplotlib as plt
import plotly.express as px
from datetime import datetime
import numpy as np
import io
import requests
from sqlalchemy.ext.automap import automap_base
from sqlalchemy.orm import Session
from sqlalchemy import create_engine, inspect
from flask import Flask, jsonify, render_template
import json


In [2]:
us_link= 'https://raw.githubusercontent.com/nytimes/covid-19-data/master/us-states.csv'
counties_link= 'https://raw.githubusercontent.com/nytimes/covid-19-data/master/us-counties.csv'

In [3]:
counties_data= pd.read_csv(counties_link)
us_data=pd.read_csv(us_link)

In [4]:
counties_data.head()

date     county       state     fips  cases  deaths
0  2020-01-21  Snohomish  Washington  53061.0      1     0.0
1  2020-01-22  Snohomish  Washington  53061.0      1     0.0
2  2020-01-23  Snohomish  Washington  53061.0      1     0.0
3  2020-01-24       Cook    Illinois  17031.0      1     0.0
4  2020-01-24  Snohomish  Washington  53061.0      1     0.0

In [5]:
us_data.head()

date       state  fips  cases  deaths
0  2020-01-21  Washington    53      1       0
1  2020-01-22  Washington    53      1       0
2  2020-01-23  Washington    53      1       0
3  2020-01-24    Illinois    17      1       0
4  2020-01-24  Washington    53      1       0

In [6]:
us_states= us_data.copy()

In [7]:
us_states.rename(columns = {'datetime':'date'}, inplace = True) 
# us_states['date_as_str'] = us_states['date'].strftime("%b-%d-%Y")

us_states.head()

date       state  fips  cases  deaths
0  2020-01-21  Washington    53      1       0
1  2020-01-22  Washington    53      1       0
2  2020-01-23  Washington    53      1       0
3  2020-01-24    Illinois    17      1       0
4  2020-01-24  Washington    53      1       0

In [8]:
us_states.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 15139 entries, 0 to 15138
Data columns (total 5 columns):
 #   Column  Non-Null Count  Dtype 
---  ------  --------------  ----- 
 0   date    15139 non-null  object
 1   state   15139 non-null  object
 2   fips    15139 non-null  int64 
 3   cases   15139 non-null  int64 
 4   deaths  15139 non-null  int64 
dtypes: int64(3), object(2)
memory usage: 591.5+ KB


In [9]:
states_cases= us_states.pivot(index=['date'], columns='state', values='cases')
states_cases=states_cases.fillna(0).reset_index()
states_cases.head()

state        date  Alabama  Alaska  Arizona  Arkansas  California  Colorado  \
0      2020-01-21      0.0     0.0      0.0       0.0         0.0       0.0   
1      2020-01-22      0.0     0.0      0.0       0.0         0.0       0.0   
2      2020-01-23      0.0     0.0      0.0       0.0         0.0       0.0   
3      2020-01-24      0.0     0.0      0.0       0.0         0.0       0.0   
4      2020-01-25      0.0     0.0      0.0       0.0         1.0       0.0   

state  Connecticut  Delaware  District of Columbia  ...  Tennessee  Texas  \
0              0.0       0.0                   0.0  ...        0.0    0.0   
1              0.0       0.0                   0.0  ...        0.0    0.0   
2              0.0       0.0                   0.0  ...        0.0    0.0   
3              0.0       0.0                   0.0  ...        0.0    0.0   
4              0.0       0.0                   0.0  ...        0.0    0.0   

state  Utah  Vermont  Virgin Islands  Virginia  Washington  West Virginia  \
0       0.0      0.0             0.0       0.0         1.0            0.0   
1       0.0      0.0             0.0       0.0         1.0            0.0   
2       0.0      0.0             0.0       0.0         1.0            0.0   
3       0.0      0.0             0.0       0.0         1.0            0.0   
4       0.0      0.0             0.0       0.0         1.0            0.0   

state  Wisconsin  Wyoming  
0            0.0      0.0  
1            0.0      0.0  
2            0.0      0.0  
3            0.0      0.0  
4            0.0      0.0  

[5 rows x 56 columns]

In [12]:
states_cases2=states_cases.melt(id_vars= ['date'], var_name='state', value_name='cases')
states_cases2.head()

date    state  cases
0  2020-01-21  Alabama    0.0
1  2020-01-22  Alabama    0.0
2  2020-01-23  Alabama    0.0
3  2020-01-24  Alabama    0.0
4  2020-01-25  Alabama    0.0

In [13]:
states_cases2['date_str']=states_cases2['date'].astype(str)

In [23]:
us_state_abbrev = {
    'Alabama': 'AL',
    'Alaska': 'AK',
    'American Samoa': 'AS',
    'Arizona': 'AZ',
    'Arkansas': 'AR',
    'California': 'CA',
    'Colorado': 'CO',
    'Connecticut': 'CT',
    'Delaware': 'DE',
    'District of Columbia': 'DC',
    'Florida': 'FL',
    'Georgia': 'GA',
    'Guam': 'GU',
    'Hawaii': 'HI',
    'Idaho': 'ID',
    'Illinois': 'IL',
    'Indiana': 'IN',
    'Iowa': 'IA',
    'Kansas': 'KS',
    'Kentucky': 'KY',
    'Louisiana': 'LA',
    'Maine': 'ME',
    'Maryland': 'MD',
    'Massachusetts': 'MA',
    'Michigan': 'MI',
    'Minnesota': 'MN',
    'Mississippi': 'MS',
    'Missouri': 'MO',
    'Montana': 'MT',
    'Nebraska': 'NE',
    'Nevada': 'NV',
    'New Hampshire': 'NH',
    'New Jersey': 'NJ',
    'New Mexico': 'NM',
    'New York': 'NY',
    'North Carolina': 'NC',
    'North Dakota': 'ND',
    'Northern Mariana Islands':'MP',
    'Ohio': 'OH',
    'Oklahoma': 'OK',
    'Oregon': 'OR',
    'Pennsylvania': 'PA',
    'Puerto Rico': 'PR',
    'Rhode Island': 'RI',
    'South Carolina': 'SC',
    'South Dakota': 'SD',
    'Tennessee': 'TN',
    'Texas': 'TX',
    'Utah': 'UT',
    'Vermont': 'VT',
    'Virgin Islands': 'VI',
    'Virginia': 'VA',
    'Washington': 'WA',
    'West Virginia': 'WV',
    'Wisconsin': 'WI',
    'Wyoming': 'WY'
}
states_cases2['abbrev']=states_cases2['state'].map(us_state_abbrev)

In [24]:
states_cases2.head()

date    state  cases    date_str  log_cases category abbrev
0  2020-01-21  Alabama    0.0  2020-01-21        NaN              AL
1  2020-01-22  Alabama    0.0  2020-01-22        NaN              AL
2  2020-01-23  Alabama    0.0  2020-01-23        NaN              AL
3  2020-01-24  Alabama    0.0  2020-01-24        NaN              AL
4  2020-01-25  Alabama    0.0  2020-01-25        NaN              AL

In [25]:
states_cases2['log_cases']=np.log(states_cases2['cases'])
states_cases2.replace([np.inf, -np.inf], np.nan, inplace=True) 

C:\Users\ellen\AppData\Roaming\Python\Python38\site-packages\pandas\core\series.py:726: RuntimeWarning: divide by zero encountered in log
  result = getattr(ufunc, method)(*inputs, **kwargs)


In [26]:
states_cases2.fillna(0).tail()

date    state    cases    date_str  log_cases category abbrev
17430  2020-11-28  Wyoming  31929.0  2020-11-28  10.371270              WY
17431  2020-11-29  Wyoming  32489.0  2020-11-29  10.388657              WY
17432  2020-11-30  Wyoming  33305.0  2020-11-30  10.413463              WY
17433  2020-12-01  Wyoming  33805.0  2020-12-01  10.428364              WY
17434  2020-12-02  Wyoming  34507.0  2020-12-02  10.448917              WY

In [27]:
states_cases2['category'] = ''

#categorizing the number of cases and assign each category to each row
def set_cat(row):
    if row['cases'] == 0:
        return '0'
    if row['cases'] > 0 and row['cases'] <= 1000:
        return '1 - 1,000'
    if row['cases'] > 1000 and row['cases'] <= 5001:
        return '1,001 - 5,000'
    if row['cases'] > 5000 and row['cases'] <= 10001:
        return '5,001 - 10,000'
    if row['cases'] > 10000 and row['cases'] <= 50001:
        return '10,001 - 50,000'
    if row['cases'] > 50000 and row['cases'] <= 100001:
        return '50,001 - 100,000'
    if row['cases'] > 100000 and row['cases'] <= 500001:
        return '100,001 -500,000'
    if row['cases'] > 500001 and row['cases'] <= 1000001:
        return '500,001 -1,000,000'
    if row['cases'] > 1000001:
        return '1,000,000+'

states_cases3 = states_cases2.assign(category=states_cases2.apply(set_cat, axis=1))

# Adds all available categories to each time frame
catg = states_cases3['category'].unique()
dts = states_cases3['date_str'].unique()

for tf in dts:
    for i in catg:
        states_cases3 = states_cases3.append({
            'date_str' : tf,
            'cases' : 'N',
            'category' : i
        }, ignore_index=True)
states_cases3.sample(10)

date        state  cases    date_str  log_cases  \
18003         NaN          NaN      N  2020-03-24        NaN   
8353   2020-05-11     Missouri  10025  2020-05-11   9.212837   
14394  2020-05-29    Tennessee  22199  2020-05-29  10.007803   
10260  2020-05-16   New Mexico   5847  2020-05-16   8.673684   
1059   2020-05-08     Arkansas   3747  2020-05-08   8.228711   
4383   2020-10-09        Idaho  47674  2020-10-09  10.772141   
2886   2020-02-23      Florida      0  2020-02-23        NaN   
2064   2020-07-01  Connecticut  46572  2020-07-01  10.748755   
16020  2020-07-09     Virginia  67988  2020-07-09  11.127086   
17970         NaN          NaN      N  2020-03-20        NaN   

               category abbrev  
18003         1 - 1,000    NaN  
8353    10,001 - 50,000     MO  
14394   10,001 - 50,000     TN  
10260    5,001 - 10,000     NM  
1059      1,001 - 5,000     AR  
4383    10,001 - 50,000     ID  
2886                  0     FL  
2064    10,001 - 50,000     CT  
16020  50,001 - 100,000     VA  
17970   10,001 - 50,000    NaN

In [34]:
# Postgres username, password, and database name
POSTGRES_ADDRESS = 'ec2-34-239-241-25.compute-1.amazonaws.com' ## INSERT YOUR DB ADDRESS IF IT'S NOT ON PANOPLY
POSTGRES_PORT = '5439'
POSTGRES_USERNAME = 'hdsqfkpfyrmcls' ## CHANGE THIS TO YOUR PANOPLY/POSTGRES USERNAME
POSTGRES_PASSWORD = '44d0c2afaa4b73f05e08bd94b4604fdb7b43432e1260f0ee78d4fbf9adae54d2' ## CHANGE THIS TO YOUR PANOPLY/POSTGRES PASSWORD POSTGRES_DBNAME = 'database' ## CHANGE THIS TO YOUR DATABASE NAME
POSTGRES_DBNAME='ddnn9438k8o9n9'
# A long string that contains the necessary Postgres login information
postgres_str = ('postgresql://{username}:{password}@{ipaddress}:{port}/{dbname}'
                .format(username=POSTGRES_USERNAME,
                        password=POSTGRES_PASSWORD,
                        ipaddress=POSTGRES_ADDRESS,
                        port=POSTGRES_PORT,
                        dbname=POSTGRES_DBNAME)) 
# Create the connection
cnx = create_engine(postgres_str)


In [ ]:
pd.read_sql_query('DROP TABLE ', cnx)

In [28]:
# # create state-level animated chloropleth

# fig =px.choropleth(states_cases3, 
#                    locations = 'abbrev', 
#                    animation_frame="date_str",
#                    color="category",
#                    color_discrete_map={
#                         '0': '#fffcfc',
#                         '1 - 1,000' : '#0d0887',
#                         '1,001 - 5,000' : '#46039f',
#                         '5,001 - 10,000' : '#7201a8',
#                         '10,001 - 50,000' : '#9c179e',
#                         '50,001 - 100,000' : '#bd3786',
#                         '100,001 - 500,000' : '#d8576b',
#                         '500,000 - 1,000,000': '#fdca26',
#                         '1,000,001+':'#f0f921'},
# #                    , , , , , , , 
#                     category_orders={
#                       'category' : [
#                           '0',
#                           '1 - 1,000',
#                           '1,001 - 5,000',
#                           '5,001 - 10,000',
#                           '10,001 - 50,000',
#                           '50,001 - 100,000',
#                           '100,001 - 500,000',
#                           '500,001 - 1,000,000',
#                           '1,000,001+'
#                       ]
#                     },
#                     title='<b>COVID-19 cases in U.S. States</b>',
#                     labels={'cases' : 'Number of Cases',
#                             'category' : 'category'},
#                     hover_name='abbrev',
#                     hover_data={
#                         'cases' : True,
#                     },
    
#                   locationmode='USA-states',
#                   scope="usa",
#                   height=600
#                  )

In [29]:
# fig.show()

In [ ]:
# fig2 = px.bar(states_cases2, x="abbrev", y="cases", color="abbrev",
#   animation_frame="date_str", animation_group="abbrev", range_y=[0,1500000], height=900)


In [ ]:
# fig2.update_xaxes(tickfont=dict(size=10))